In [ ]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from pandas.api.types import is_numeric_dtype
import warnings
from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import MinMaxScaler
from sklearn.tree  import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import BernoulliNB
from sklearn.feature_selection import RFE
import itertools
from tabulate import tabulate
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder
import plotly.express as px
import plotly.graph_objects as go

### **Reading Data**

In [ ]:
train=pd.read_csv(r'/content/Train_data.csv')

In [ ]:
test=pd.read_csv(r'/content/Test_data.csv')

In [ ]:
train.head()

duration protocol_type   service flag  src_bytes  dst_bytes  land  \
0         0           tcp  ftp_data   SF        491          0     0   
1         0           udp     other   SF        146          0     0   
2         0           tcp   private   S0          0          0     0   
3         0           tcp      http   SF        232       8153     0   
4         0           tcp      http   SF        199        420     0   

   wrong_fragment  urgent  hot  ...  dst_host_srv_count  \
0               0       0    0  ...                  25   
1               0       0    0  ...                   1   
2               0       0    0  ...                  26   
3               0       0    0  ...                 255   
4               0       0    0  ...                 255   

   dst_host_same_srv_rate  dst_host_diff_srv_rate  \
0                    0.17                    0.03   
1                    0.00                    0.60   
2                    0.10                    0.05   
3                    1.00                    0.00   
4                    1.00                    0.00   

   dst_host_same_src_port_rate  dst_host_srv_diff_host_rate  \
0                         0.17                         0.00   
1                         0.88                         0.00   
2                         0.00                         0.00   
3                         0.03                         0.04   
4                         0.00                         0.00   

   dst_host_serror_rate  dst_host_srv_serror_rate  dst_host_rerror_rate  \
0                  0.00                      0.00                  0.05   
1                  0.00                      0.00                  0.00   
2                  1.00                      1.00                  0.00   
3                  0.03                      0.01                  0.00   
4                  0.00                      0.00                  0.00   

   dst_host_srv_rerror_rate    class  
0                      0.00   normal  
1                      0.00   normal  
2                      0.00  anomaly  
3                      0.01   normal  
4                      0.00   normal  

[5 rows x 42 columns]

In [ ]:
test.head()

duration protocol_type   service  flag  src_bytes  dst_bytes  land  \
0         0           tcp   private   REJ          0          0     0   
1         0           tcp   private   REJ          0          0     0   
2         2           tcp  ftp_data    SF      12983          0     0   
3         0          icmp     eco_i    SF         20          0     0   
4         1           tcp    telnet  RSTO          0         15     0   

   wrong_fragment  urgent  hot  ...  dst_host_count  dst_host_srv_count  \
0               0       0    0  ...             255                  10   
1               0       0    0  ...             255                   1   
2               0       0    0  ...             134                  86   
3               0       0    0  ...               3                  57   
4               0       0    0  ...              29                  86   

   dst_host_same_srv_rate  dst_host_diff_srv_rate  \
0                    0.04                    0.06   
1                    0.00                    0.06   
2                    0.61                    0.04   
3                    1.00                    0.00   
4                    0.31                    0.17   

   dst_host_same_src_port_rate  dst_host_srv_diff_host_rate  \
0                         0.00                         0.00   
1                         0.00                         0.00   
2                         0.61                         0.02   
3                         1.00                         0.28   
4                         0.03                         0.02   

   dst_host_serror_rate  dst_host_srv_serror_rate  dst_host_rerror_rate  \
0                   0.0                       0.0                  1.00   
1                   0.0                       0.0                  1.00   
2                   0.0                       0.0                  0.00   
3                   0.0                       0.0                  0.00   
4                   0.0                       0.0                  0.83   

   dst_host_srv_rerror_rate  
0                      1.00  
1                      1.00  
2                      0.00  
3                      0.00  
4                      0.71  

[5 rows x 41 columns]

### **Data Preprocessing**

In [ ]:
# Compare columns in train and test
print('Columns in train but not in test:', set(train.columns)-set(test.columns))
print('Columns in test but not in train:', set(test.columns)-set(train.columns))

Columns in train but not in test: {'class'}
Columns in test but not in train: set()


Perfect!

**Checking Null Values**

In [ ]:
for i in train.columns:
    # Check Any NA Values
    if train[i].isnull().sum() > 0:
        print(i, train[i].isnull().sum())

In [ ]:
for i  in test.columns:
    # Check Any NA Values
    if test[i].isnull().sum() > 0:
        print(i, test[i].isnull().sum())

No Null Values in Train Dataset as well as Test Dataset

In [ ]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25192 entries, 0 to 25191
Data columns (total 42 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   duration                     25192 non-null  int64  
 1   protocol_type                25192 non-null  object 
 2   service                      25192 non-null  object 
 3   flag                         25192 non-null  object 
 4   src_bytes                    25192 non-null  int64  
 5   dst_bytes                    25192 non-null  int64  
 6   land                         25192 non-null  int64  
 7   wrong_fragment               25192 non-null  int64  
 8   urgent                       25192 non-null  int64  
 9   hot                          25192 non-null  int64  
 10  num_failed_logins            25192 non-null  int64  
 11  logged_in                    25192 non-null  int64  
 12  num_compromised              25192 non-null  int64  
 13  root_shell      

**Further Processing**

In [ ]:
# Get Numeric Columns
numeric_columns = train.select_dtypes(include=[np.number]).columns
other_columns = train.columns.difference(numeric_columns)

In [ ]:
len(numeric_columns), len(other_columns)

(38, 4)

In [ ]:
print("NUMERIC COLUMNS:", numeric_columns)
print("OTHER COLUMNS:", other_columns)

NUMERIC COLUMNS: Index(['duration', 'src_bytes', 'dst_bytes', 'land', 'wrong_fragment',
       'urgent', 'hot', 'num_failed_logins', 'logged_in', 'num_compromised',
       'root_shell', 'su_attempted', 'num_root', 'num_file_creations',
       'num_shells', 'num_access_files', 'num_outbound_cmds', 'is_host_login',
       'is_guest_login', 'count', 'srv_count', 'serror_rate',
       'srv_serror_rate', 'rerror_rate', 'srv_rerror_rate', 'same_srv_rate',
       'diff_srv_rate', 'srv_diff_host_rate', 'dst_host_count',
       'dst_host_srv_count', 'dst_host_same_srv_rate',
       'dst_host_diff_srv_rate', 'dst_host_same_src_port_rate',
       'dst_host_srv_diff_host_rate', 'dst_host_serror_rate',
       'dst_host_srv_serror_rate', 'dst_host_rerror_rate',
       'dst_host_srv_rerror_rate'],
      dtype='object')
OTHER COLUMNS: Index(['class', 'flag', 'protocol_type', 'service'], dtype='object')


In [ ]:
output_column = 'class'
other_columns = other_columns.difference([output_column])

In [ ]:
numeric_columns, other_columns, output_column

(Index(['duration', 'src_bytes', 'dst_bytes', 'land', 'wrong_fragment',
        'urgent', 'hot', 'num_failed_logins', 'logged_in', 'num_compromised',
        'root_shell', 'su_attempted', 'num_root', 'num_file_creations',
        'num_shells', 'num_access_files', 'num_outbound_cmds', 'is_host_login',
        'is_guest_login', 'count', 'srv_count', 'serror_rate',
        'srv_serror_rate', 'rerror_rate', 'srv_rerror_rate', 'same_srv_rate',
        'diff_srv_rate', 'srv_diff_host_rate', 'dst_host_count',
        'dst_host_srv_count', 'dst_host_same_srv_rate',
        'dst_host_diff_srv_rate', 'dst_host_same_src_port_rate',
        'dst_host_srv_diff_host_rate', 'dst_host_serror_rate',
        'dst_host_srv_serror_rate', 'dst_host_rerror_rate',
        'dst_host_srv_rerror_rate'],
       dtype='object'),
 Index(['flag', 'protocol_type', 'service'], dtype='object'),
 'class')

**One Hot Encoding**

In [ ]:
# Number of Distinct Values in Each Column
for i in other_columns:
    print(i, " -> Number of Distinct Values:", train[i].nunique())

flag  -> Number of Distinct Values: 11
protocol_type  -> Number of Distinct Values: 3
service  -> Number of Distinct Values: 66


In [ ]:
train = pd.get_dummies(train, columns=other_columns, drop_first=True)

In [ ]:
train.head()

duration  src_bytes  dst_bytes  land  wrong_fragment  urgent  hot  \
0         0        491          0     0               0       0    0   
1         0        146          0     0               0       0    0   
2         0          0          0     0               0       0    0   
3         0        232       8153     0               0       0    0   
4         0        199        420     0               0       0    0   

   num_failed_logins  logged_in  num_compromised  ...  service_systat  \
0                  0          0                0  ...           False   
1                  0          0                0  ...           False   
2                  0          0                0  ...           False   
3                  0          1                0  ...           False   
4                  0          1                0  ...           False   

   service_telnet  service_tim_i  service_time  service_urh_i  service_urp_i  \
0           False          False         False          False          False   
1           False          False         False          False          False   
2           False          False         False          False          False   
3           False          False         False          False          False   
4           False          False         False          False          False   

   service_uucp  service_uucp_path  service_vmnet  service_whois  
0         False              False          False          False  
1         False              False          False          False  
2         False              False          False          False  
3         False              False          False          False  
4         False              False          False          False  

[5 rows x 116 columns]

In [ ]:
train.columns

Index(['duration', 'src_bytes', 'dst_bytes', 'land', 'wrong_fragment',
       'urgent', 'hot', 'num_failed_logins', 'logged_in', 'num_compromised',
       ...
       'service_systat', 'service_telnet', 'service_tim_i', 'service_time',
       'service_urh_i', 'service_urp_i', 'service_uucp', 'service_uucp_path',
       'service_vmnet', 'service_whois'],
      dtype='object', length=116)

**TRAIN TEST SPLIT**

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(train.drop('class', axis=1), train['class'], test_size=0.2, random_state=42, stratify=train['class'])

In [ ]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((20153, 115), (5039, 115), (20153,), (5039,))

**NORMALISATION**

In [ ]:
min_max_scaler = MinMaxScaler()
X_train = min_max_scaler.fit_transform(X_train)
X_test = min_max_scaler.transform(X_test)

In [ ]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((20153, 115), (5039, 115), (20153,), (5039,))

In [ ]:
X_train[0]

array([0.00000000e+00, 7.72839861e-07, 2.47913911e-03, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       1.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 1.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       1.00000000e+00, 1.00000000e+00, 1.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 1.00000000e+00, 0.00000000e+00,
       1.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
       0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
      

In [ ]:
y_train[0]

'normal'

**Visualizing in 3-Dimensions**

In [ ]:
# Visualize the Data in 3 dimensions using TSNE
from sklearn.manifold import TSNE
tsne = TSNE(n_components=3, random_state=42)
X_train_3d_tsne = tsne.fit_transform(X_train)

X_train_3d_tsne.shape

(20153, 3)

In [ ]:
colors = ['red' if i == 'normal' else 'blue' for i in y_train]

In [ ]:
# Visualize the Data in 3 dimensions via Plotly using TSNE, Mark y_train[i] = 'normal' as red and y_train[i] = 'anomaly' as blue
fig = go.Figure()
fig.add_trace(go.Scatter3d(x=X_train_3d_tsne[:, 0], y=X_train_3d_tsne[:, 1], z=X_train_3d_tsne[:, 2], mode='markers', marker=dict(color=colors)))
fig.show()

Clear Pattern Seems to be Visible.

In [ ]:
# Visualize the Data in 2 dimensions using TSNE
tsne = TSNE(n_components=2, random_state=42)
X_train_2d_tsne = tsne.fit_transform(X_train)

X_train_2d_tsne.shape

(20153, 2)

In [ ]:
# Visualize the Data in 2 dimensions via Plotly using TSNE, Mark y_train[i] = 'normal' as red and y_train[i] = 'anomaly' as blue
fig = go.Figure()
fig.add_trace(go.Scatter(x=X_train_2d_tsne[:, 0], y=X_train_2d_tsne[:, 1], mode='markers', marker=dict(color=colors)))
fig.show()

### **UNSUPERVISED TECHNIQUES BASED ON ALL FEATURES**

We will use 3 techniques for anomaly detection [**Out of which 2 Dont work for this problem**]:

1. **Isolation Forest** : It is an unsupervised learning algorithm that belongs to the ensemble decision trees family. It is based on the Decision Tree algorithm. In these methods, the decision tree is used to isolate each observation. This method is highly useful for detecting anomalies in the data - $Wont$ $work$ as in our data, anomalies are not in minority.

2. **Local Outlier Factor** : The LOF algorithm is an unsupervised outlier detection method which computes the local density deviation of a given data point with respect to its neighbors. It considers as outlier samples that have a substantially lower density than their neighbors - $Wont$ $work$ as in our data, anomalies are not in minority.

3. **DBSCAN** : DBSCAN is a density-based clustering non-parametric algorithm: given a set of points in some space, it groups together points that are closely packed together (points with many nearby neighbors), marking as outliers points that lie alone in low-density regions (whose nearest neighbors are too far away) - $Can$ $work$ as it is based on density and can separate anomalies from normal data.

In [ ]:
y_train.value_counts()

class
normal     10759
anomaly     9394
Name: count, dtype: int64

In [ ]:
y_test.value_counts()

class
normal     2690
anomaly    2349
Name: count, dtype: int64

In [ ]:
# ISOLATION FOREST
from sklearn.ensemble import IsolationForest
isolation_forest = IsolationForest(n_estimators=100, random_state=42)

In [ ]:
isolation_forest.fit(X_train)

IsolationForest(random_state=42)

In [ ]:
y_pred_train = isolation_forest.predict(X_train)
y_pred_test = isolation_forest.predict(X_test)

In [ ]:
y_pred_train.shape, y_pred_test.shape, y_train.shape, y_test.shape

((20153,), (5039,), (20153,), (5039,))

In [ ]:
np.unique(y_pred_train, return_counts=True)

(array([-1,  1]), array([   16, 20137]))

In [ ]:
# Anomaly Detection
# -1 -> Anomaly
# 1 -> Normal
y_pred_train = np.where(y_pred_train == -1, 'anomaly', 'normal')
y_pred_test = np.where(y_pred_test == -1, 'anomaly', 'normal')

In [ ]:
# Classification Report
from sklearn.metrics import classification_report

In [ ]:
print("TRAIN CLASSIFICATION REPORT")
print(classification_report(y_train, y_pred_train))

TRAIN CLASSIFICATION REPORT
              precision    recall  f1-score   support

     anomaly       0.31      0.00      0.00      9394
      normal       0.53      1.00      0.70     10759

    accuracy                           0.53     20153
   macro avg       0.42      0.50      0.35     20153
weighted avg       0.43      0.53      0.37     20153



In [ ]:
# Classification Report
print("TEST CLASSIFICATION REPORT")
print(classification_report(y_test, y_pred_test))

TEST CLASSIFICATION REPORT
              precision    recall  f1-score   support

     anomaly       0.33      0.00      0.00      2349
      normal       0.53      1.00      0.70      2690

    accuracy                           0.53      5039
   macro avg       0.43      0.50      0.35      5039
weighted avg       0.44      0.53      0.37      5039



In [ ]:
# Adjusted Rand Index
from sklearn.metrics import adjusted_rand_score

adjusted_rand_score(y_train, y_pred_train), adjusted_rand_score(y_test, y_pred_test)

(-6.620882242378021e-05, -8.635531018342895e-05)

In [ ]:
# LOF
from sklearn.neighbors import LocalOutlierFactor

lof = LocalOutlierFactor(n_neighbors=20)

In [ ]:
lof.fit(X_train)

LocalOutlierFactor()

In [ ]:
y_pred_train = lof.fit_predict(X_train)
y_pred_test = lof.fit_predict(X_test)

In [ ]:
# Unique Values
np.unique(y_pred_train, return_counts=True)

(array([-1,  1]), array([ 3019, 17134]))

In [ ]:
# Adjusted Rand Index
adjusted_rand_score(y_train, y_pred_train), adjusted_rand_score(y_test, y_pred_test)

(-0.0008591460201811297, 0.01846259698804876)

In [ ]:
# Anomaly Detection
# -1 -> Anomaly
# 1 -> Normal
y_pred_train = np.where(y_pred_train == -1, 'anomaly', 'normal')
y_pred_test = np.where(y_pred_test == -1, 'anomaly', 'normal')

In [ ]:
# Classification Report
print("TRAIN CLASSIFICATION REPORT")
print(classification_report(y_train, y_pred_train))

TRAIN CLASSIFICATION REPORT
              precision    recall  f1-score   support

     anomaly       0.45      0.14      0.22      9394
      normal       0.53      0.85      0.65     10759

    accuracy                           0.52     20153
   macro avg       0.49      0.50      0.44     20153
weighted avg       0.49      0.52      0.45     20153



In [ ]:
# Classification Report
print("TEST CLASSIFICATION REPORT")
print(classification_report(y_test, y_pred_test))

TEST CLASSIFICATION REPORT
              precision    recall  f1-score   support

     anomaly       0.58      0.30      0.39      2349
      normal       0.57      0.81      0.67      2690

    accuracy                           0.57      5039
   macro avg       0.57      0.55      0.53      5039
weighted avg       0.57      0.57      0.54      5039



**Still POOR**

### **DBSCAN**

In [ ]:
# DBSCAN
from sklearn.cluster import DBSCAN

dbscan = DBSCAN(eps=0.5, min_samples=5)

In [ ]:
dbscan.fit(X_train)

DBSCAN()

In [ ]:
y_pred_train = dbscan.fit_predict(X_train)
y_pred_test = dbscan.fit_predict(X_test)

In [ ]:
# Unique Values
y_pred_train.shape, y_pred_test.shape

((20153,), (5039,))

In [ ]:
y_pred_train

array([  0,  -1,   1, ...,   2, 114, 140])

In [ ]:
# Adjusted Rand Index
adjusted_rand_score(y_train, y_pred_train), adjusted_rand_score(y_test, y_pred_test)

(0.17912447916225435, 0.16924404315876476)

**Best of the 3** as we thought

#### **Possible Issue:**

We are treating the problem as anomaly detection, but it is not as 'anomaly' class is not in minority [not a real anomaly] - We should instead take out important features and do **Binary Classification** to get high accuracy on this dataset.

We are using the entire feature set for anomaly detection, which is not a good idea. We should use only the important features for anomaly detection.

To Find Important Features, we can do:

1. **Feature Importance** : We can use Random Forest to find the important features.

2. **PCA** : We can use PCA to find the important features.

3. **Autoencoders** : We can use Autoencoders to find the important features.

Also, Need to remove intercorrelated features.

In [ ]:
NUMBER_IMPORTANT_FEATURES_TO_GET = 50

#### **Random Forest Important Features**

In [ ]:
# Find Important Features using Random Forest
random_forest = RandomForestClassifier(n_estimators=100, random_state=42)
random_forest.fit(X_train, y_train)

RandomForestClassifier(random_state=42)

In [ ]:
random_forest.feature_importances_

array([3.74314659e-03, 1.26139066e-01, 1.37970060e-01, 1.91378790e-05,
       2.52826251e-03, 5.84842063e-05, 8.74793884e-03, 1.86130573e-04,
       4.68290425e-02, 6.62694527e-03, 1.80346119e-04, 4.11101168e-05,
       5.49179430e-04, 2.41130762e-04, 3.84264891e-05, 1.05146475e-04,
       0.00000000e+00, 0.00000000e+00, 7.07902842e-04, 2.83927930e-02,
       1.49657750e-02, 2.04070147e-02, 2.36243064e-02, 1.05005282e-02,
       4.39740740e-03, 4.92563348e-02, 4.03820543e-02, 5.56917102e-03,
       2.63458692e-02, 2.78570154e-02, 4.94238161e-02, 5.22849850e-02,
       2.85008178e-02, 1.49170376e-02, 2.12501774e-02, 3.93205668e-02,
       1.68963102e-02, 1.07670066e-02, 1.35452652e-03, 2.44450749e-04,
       1.34097723e-05, 1.99157459e-03, 1.45291521e-02, 5.50942546e-04,
       7.68351594e-05, 3.73068854e-06, 4.66728998e-02, 1.57912750e-04,
       1.47839327e-02, 1.11536479e-02, 9.48807854e-05, 1.87077628e-06,
       1.33734699e-04, 9.98288631e-10, 7.59508085e-10, 1.02079652e-07,
      

In [ ]:
# Pick top - 10
important_features_rfe = random_forest.feature_importances_
important_features_rfe = important_features_rfe.argsort()[::-1][:NUMBER_IMPORTANT_FEATURES_TO_GET]

In [ ]:
important_features_rfe, random_forest.feature_importances_[important_features_rfe]

(array([  2,   1,  31,  30,  25,   8,  46,  26,  35,  71,  32,  19,  29,
         28,  22,  34,  21,  36,  20,  33,  48,  42,  62,  95,  49,  63,
         37,  23,   6,   9,  68,  60,  27,  24,   0, 100,   4,  90,  41,
        110,  38,  67,  18, 106,  43,  12,  66,  39,  13,   7]),
 array([0.13797006, 0.12613907, 0.05228498, 0.04942382, 0.04925633,
        0.04682904, 0.0466729 , 0.04038205, 0.03932057, 0.02883843,
        0.02850082, 0.02839279, 0.02785702, 0.02634587, 0.02362431,
        0.02125018, 0.02040701, 0.01689631, 0.01496577, 0.01491704,
        0.01478393, 0.01452915, 0.01426348, 0.01138717, 0.01115365,
        0.01089133, 0.01076701, 0.01050053, 0.00874794, 0.00662695,
        0.00650049, 0.00637212, 0.00556917, 0.00439741, 0.00374315,
        0.00365962, 0.00252826, 0.00229696, 0.00199157, 0.00154375,
        0.00135453, 0.0008746 , 0.0007079 , 0.00056607, 0.00055094,
        0.00054918, 0.00041335, 0.00024445, 0.00024113, 0.00018613]))

In [ ]:
X_train_rfe = X_train[:, important_features_rfe]
X_test_rfe = X_test[:, important_features_rfe]

In [ ]:
X_train_rfe.shape, X_test_rfe.shape

((20153, 50), (5039, 50))

#### **PCA Important Features**

In [ ]:
# Use PCA for find important features
from sklearn.decomposition import PCA

pca = PCA(n_components=NUMBER_IMPORTANT_FEATURES_TO_GET)
X_train_pca = pca.fit_transform(X_train)
X_test_pca = pca.transform(X_test)

In [ ]:
X_train_pca.shape

(20153, 50)

In [ ]:
# Find Important Features using PCA
pca.explained_variance_ratio_

array([0.42012571, 0.15893223, 0.10702746, 0.04838125, 0.03903922,
       0.02824248, 0.02105838, 0.01691001, 0.01497873, 0.01398697,
       0.01146688, 0.00961659, 0.0068889 , 0.00656151, 0.00593801,
       0.00539958, 0.00465044, 0.0039967 , 0.00379659, 0.00343807,
       0.00326392, 0.00293214, 0.00237444, 0.00222507, 0.0020399 ,
       0.00188753, 0.00180477, 0.00172678, 0.00160973, 0.00149875,
       0.00148744, 0.00140765, 0.00137683, 0.00137401, 0.00133694,
       0.00131161, 0.001269  , 0.00123603, 0.00118872, 0.00116479,
       0.00113017, 0.00112112, 0.00111432, 0.00109801, 0.00107543,
       0.00106532, 0.00105018, 0.00104935, 0.00102911, 0.00102721])

In [ ]:
X_train_pca.shape, X_test_pca.shape

((20153, 50), (5039, 50))

#### **Autoencoders Important Features**

In [ ]:
X_train.shape, X_test.shape

((20153, 115), (5039, 115))

In [ ]:
# Autoencoder Batch Normalization
from keras.models import Model
from keras.layers import Input, Dense, BatchNormalization

input_layer = Input(shape=(X_train.shape[1],))
encoded = Dense(100, activation='relu')(input_layer)
encoded = BatchNormalization()(encoded)
encoded = Dense(50, activation='relu')(encoded)
encoded = BatchNormalization()(encoded)
encoded = Dense(25, activation='relu')(encoded)
encoded = BatchNormalization()(encoded)
decoded = Dense(50, activation='relu')(encoded)
decoded = BatchNormalization()(decoded)
decoded = Dense(100, activation='relu')(decoded)
decoded = BatchNormalization()(decoded)
decoded = Dense(X_train.shape[1], activation='sigmoid')(decoded)

autoencoder = Model(input_layer, decoded)
autoencoder.compile(optimizer='adam', loss='mse')

In [ ]:
autoencoder.fit(X_train, X_train, epochs=100, batch_size=1024, validation_data=(X_test, X_test))

Epoch 1/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 6s 47ms/step - loss: 0.2635 - val_loss: 0.2319
Epoch 2/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - loss: 0.2150 - val_loss: 0.2026
Epoch 3/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - loss: 0.1796 - val_loss: 0.1507
Epoch 4/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - loss: 0.1290 - val_loss: 0.0871
Epoch 5/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - loss: 0.0791 - val_loss: 0.0483
Epoch 6/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 49ms/step - loss: 0.0504 - val_loss: 0.0337
Epoch 7/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 2s 74ms/step - loss: 0.0370 - val_loss: 0.0279
Epoch 8/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 49ms/step - loss: 0.0327 - val_loss: 0.0245
Epoch 9/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 45ms/step - loss: 0.0301 - val_loss: 0.0219
Epoch 10/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - loss: 0.0271 - val_loss: 0.0199
Epoch 11/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - loss: 0.0259 - val_loss: 0.0181
Epoch 12/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step

In [ ]:
encoder = Model(input_layer, encoded)

X_train_autoencoder = encoder.predict(X_train)
X_test_autoencoder = encoder.predict(X_test)

630/630 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step
158/158 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step


In [ ]:
X_train_autoencoder.shape, X_test_autoencoder.shape

((20153, 25), (5039, 25))

**NOTE:** We can also try anomaly detection using autoencoders - Reconstruction Error > Threshold => Anomaly as less inputs for anomalies => Model will not be able to reconstruct properly. But it is wont work as 'anomaly' class is not minority [real anomaly].

### PLAN AHEAD:

**Maybe Above 3 Method with Important Features** : We can use the above 3 methods with important features to get better results - Might not work as we saw above our problem is not really anomaly detection in the data but it is actually **Binary Classification Problem**

**Binary Classification** : We can use the important features to do binary classification and get high accuracy on this dataset - Use Random Forest, XGBoost, AdaBoost, ANN, Voting Classifier, etc.



### $$**BINARY-CLASSIFICATION**$$

#### **Random Forest**

In [ ]:
# Random Forest Binary Classification based on all 3 feature sets
random_forest_rfe = RandomForestClassifier(n_estimators=100, random_state=42)
random_forest_pca = RandomForestClassifier(n_estimators=100, random_state=42)
random_forest_autoencoder = RandomForestClassifier(n_estimators=100, random_state=42)

In [ ]:
random_forest_rfe.fit(X_train_rfe, y_train)
random_forest_pca.fit(X_train_pca, y_train)
random_forest_autoencoder.fit(X_train_autoencoder, y_train)

RandomForestClassifier(random_state=42)

In [ ]:
y_pred_train_rfe = random_forest_rfe.predict(X_train_rfe)
y_pred_test_rfe = random_forest_rfe.predict(X_test_rfe)

y_pred_train_pca = random_forest_pca.predict(X_train_pca)
y_pred_test_pca = random_forest_pca.predict(X_test_pca)

y_pred_train_autoencoder = random_forest_autoencoder.predict(X_train_autoencoder)
y_pred_test_autoencoder = random_forest_autoencoder.predict(X_test_autoencoder)

In [ ]:
# Classification Report
print("TRAIN CLASSIFICATION REPORT")
print("RFE")
print(classification_report(y_train, y_pred_train_rfe))
print("PCA")
print(classification_report(y_train, y_pred_train_pca))
print("AUTOENCODER")
print(classification_report(y_train, y_pred_train_autoencoder))

TRAIN CLASSIFICATION REPORT
RFE
              precision    recall  f1-score   support

     anomaly       1.00      1.00      1.00      9394
      normal       1.00      1.00      1.00     10759

    accuracy                           1.00     20153
   macro avg       1.00      1.00      1.00     20153
weighted avg       1.00      1.00      1.00     20153

PCA
              precision    recall  f1-score   support

     anomaly       1.00      1.00      1.00      9394
      normal       1.00      1.00      1.00     10759

    accuracy                           1.00     20153
   macro avg       1.00      1.00      1.00     20153
weighted avg       1.00      1.00      1.00     20153

AUTOENCODER
              precision    recall  f1-score   support

     anomaly       1.00      1.00      1.00      9394
      normal       1.00      1.00      1.00     10759

    accuracy                           1.00     20153
   macro avg       1.00      1.00      1.00     20153
weighted avg       1.00   

In [ ]:
# Classification Report
print("TEST CLASSIFICATION REPORT")
print("RFE")
print(classification_report(y_test, y_pred_test_rfe))
print("PCA")
print(classification_report(y_test, y_pred_test_pca))
print("AUTOENCODER")
print(classification_report(y_test, y_pred_test_autoencoder))

TEST CLASSIFICATION REPORT
RFE
              precision    recall  f1-score   support

     anomaly       1.00      1.00      1.00      2349
      normal       1.00      1.00      1.00      2690

    accuracy                           1.00      5039
   macro avg       1.00      1.00      1.00      5039
weighted avg       1.00      1.00      1.00      5039

PCA
              precision    recall  f1-score   support

     anomaly       1.00      0.99      0.99      2349
      normal       0.99      1.00      1.00      2690

    accuracy                           0.99      5039
   macro avg       1.00      0.99      0.99      5039
weighted avg       0.99      0.99      0.99      5039

AUTOENCODER
              precision    recall  f1-score   support

     anomaly       1.00      0.99      0.99      2349
      normal       0.99      1.00      1.00      2690

    accuracy                           0.99      5039
   macro avg       0.99      0.99      0.99      5039
weighted avg       0.99    

In [ ]:
# Accuracy
from sklearn.metrics import accuracy_score
rfe_accuracy = accuracy_score(y_test, y_pred_test_rfe)
pca_accuracy = accuracy_score(y_test, y_pred_test_pca)
autoencoder_accuracy = accuracy_score(y_test, y_pred_test_autoencoder)

In [ ]:
print("RFE Features Random Forest ACCURACY: {}%".format(round(rfe_accuracy*100, 2)))
print("PCA Features Random Forest ACCURACY: {}%".format(round(pca_accuracy*100, 2)))
print("Autoencoder Features Random Forest ACCURACY: {}%".format(round(autoencoder_accuracy*100, 2)))

RFE Features Random Forest ACCURACY: 99.78%
PCA Features Random Forest ACCURACY: 99.48%
Autoencoder Features Random Forest ACCURACY: 99.46%


Random Forest Seems to be Giving an Amazing Accuracy of $99.74%$ on Test Data. Let's try to increase it by using a neural network.

**Artificial Neural Network**

In [ ]:
# Input Shapes
X_train.shape, X_train_rfe.shape, X_train_pca.shape, X_train_autoencoder.shape

((20153, 115), (20153, 50), (20153, 50), (20153, 25))

In [ ]:
# ANN-1
from keras.models import Sequential
from keras.layers import Dense, BatchNormalization, Input

model_rfe = Sequential()
model_rfe.add(Input(shape=(X_train_rfe.shape[1],)))
model_rfe.add(Dense(50, activation='relu'))
model_rfe.add(BatchNormalization())
model_rfe.add(Dense(25, activation='relu'))
model_rfe.add(BatchNormalization())
model_rfe.add(Dense(1, activation='sigmoid'))

model_rfe.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In [ ]:
# ANN-2
model_pca = Sequential()
model_pca.add(Input(shape=(X_train_pca.shape[1],)))
model_pca.add(Dense(50, activation='relu'))
model_pca.add(BatchNormalization())
model_pca.add(Dense(25, activation='relu'))
model_pca.add(BatchNormalization())
model_pca.add(Dense(1, activation='sigmoid'))

model_pca.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In [ ]:
# ANN-3
model_autoencoder = Sequential()
model_autoencoder.add(Input(shape=(X_train_autoencoder.shape[1],)))
model_autoencoder.add(Dense(50, activation='relu'))
model_autoencoder.add(BatchNormalization())
model_autoencoder.add(Dense(25, activation='relu'))
model_autoencoder.add(BatchNormalization())
model_autoencoder.add(Dense(1, activation='sigmoid'))

model_autoencoder.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

In [ ]:
y_train = np.where(y_train == 'normal', 1, 0)
y_test = np.where(y_test == 'normal', 1, 0)

In [ ]:
# Train Models
model_rfe.fit(X_train_rfe, y_train, epochs=100, batch_size=1024, validation_data=(X_test_rfe, y_test))

Epoch 1/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 3s 32ms/step - accuracy: 0.5970 - loss: 0.8064 - val_accuracy: 0.8897 - val_loss: 0.4871
Epoch 2/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.9606 - loss: 0.1502 - val_accuracy: 0.9319 - val_loss: 0.3972
Epoch 3/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.9678 - loss: 0.1104 - val_accuracy: 0.9611 - val_loss: 0.3504
Epoch 4/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.9716 - loss: 0.0943 - val_accuracy: 0.9518 - val_loss: 0.3191
Epoch 5/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.9749 - loss: 0.0823 - val_accuracy: 0.9484 - val_loss: 0.2954
Epoch 6/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.9791 - loss: 0.0721 - val_accuracy: 0.9460 - val_loss: 0.2773
Epoch 7/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.9780 - loss: 0.0695 - val_accuracy: 0.9444 - val_loss: 0.2651
Epoch 8/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.9798 - loss: 0.0640 - val_accuracy: 0.94

In [ ]:
# Train Models
model_pca.fit(X_train_pca, y_train, epochs=100, batch_size=1024, validation_data=(X_test_pca, y_test))

Epoch 1/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 3s 33ms/step - accuracy: 0.9104 - loss: 0.3288 - val_accuracy: 0.9004 - val_loss: 0.5292
Epoch 2/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.9673 - loss: 0.1287 - val_accuracy: 0.9321 - val_loss: 0.4621
Epoch 3/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.9717 - loss: 0.0934 - val_accuracy: 0.9550 - val_loss: 0.4132
Epoch 4/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.9769 - loss: 0.0782 - val_accuracy: 0.9639 - val_loss: 0.3716
Epoch 5/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.9799 - loss: 0.0664 - val_accuracy: 0.9690 - val_loss: 0.3305
Epoch 6/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.9805 - loss: 0.0642 - val_accuracy: 0.9712 - val_loss: 0.2937
Epoch 7/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.9828 - loss: 0.0555 - val_accuracy: 0.9720 - val_loss: 0.2588
Epoch 8/100
20/20 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.9818 - loss: 0.0547 - val_accuracy: 0.974

In [ ]:
# Train Models
model_autoencoder.fit(X_train_autoencoder, y_train, epochs=100, batch_size=2048, validation_data=(X_test_autoencoder, y_test))

Epoch 1/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 2s 42ms/step - accuracy: 0.3884 - loss: 1.1823 - val_accuracy: 0.4642 - val_loss: 0.8057
Epoch 2/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.7952 - loss: 0.5079 - val_accuracy: 0.7436 - val_loss: 0.5607
Epoch 3/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - accuracy: 0.8826 - loss: 0.2957 - val_accuracy: 0.8899 - val_loss: 0.4388
Epoch 4/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.9220 - loss: 0.2289 - val_accuracy: 0.9500 - val_loss: 0.3707
Epoch 5/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.9454 - loss: 0.1867 - val_accuracy: 0.9597 - val_loss: 0.3254
Epoch 6/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.9564 - loss: 0.1589 - val_accuracy: 0.9655 - val_loss: 0.2896
Epoch 7/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step - accuracy: 0.9626 - loss: 0.1415 - val_accuracy: 0.9704 - val_loss: 0.2603
Epoch 8/100
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step - accuracy: 0.9658 - loss: 0.1347 - val_accuracy: 0.

In [ ]:
# Predictions
y_pred_test_rfe = model_rfe.predict(X_test_rfe)
y_pred_test_pca = model_pca.predict(X_test_pca)
y_pred_test_autoencoder = model_autoencoder.predict(X_test_autoencoder)

158/158 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step
158/158 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step
158/158 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step


In [ ]:
y_pred_test_rfe = np.where(y_pred_test_rfe > 0.5, 1, 0)
y_pred_test_pca = np.where(y_pred_test_pca > 0.5, 1, 0)
y_pred_test_autoencoder = np.where(y_pred_test_autoencoder > 0.5, 1, 0)

In [ ]:
# Accuracy
rfe_accuracy = accuracy_score(y_test, y_pred_test_rfe)
pca_accuracy = accuracy_score(y_test, y_pred_test_pca)
autoencoder_accuracy = accuracy_score(y_test, y_pred_test_autoencoder)

In [ ]:
print("RFE Features ANN ACCURACY: {}%".format(round(rfe_accuracy*100, 2)))
print("PCA Features ANN ACCURACY: {}%".format(round(pca_accuracy*100, 2)))
print("Autoencoder Features ANN ACCURACY: {}%".format(round(autoencoder_accuracy*100, 2)))

RFE Features ANN ACCURACY: 99.54%
PCA Features ANN ACCURACY: 99.46%
Autoencoder Features ANN ACCURACY: 98.73%


In [ ]:
import synthetic_data_generator as sdg

In [ ]:
num_nodes = 3

In [ ]:
data = np.array(sdg.generate_data(num_nodes=num_nodes, average_bytes_per_edge=20, count=10000, multiplier=5))

In [ ]:
data.shape

(10000, 3)

#### **Lets Visualize our First Network Traffic Data**

In [ ]:
# Create a Graph
import networkx as nx
G = nx.DiGraph()
# Add Nodes
G.add_nodes_from(range(1, num_nodes+1))
# Add Edges
edges = list(itertools.combinations(range(1, num_nodes+1), 2))
for i in range(len(edges)):
    G.add_edge(edges[i][0], edges[i][1], weight=data[0][i])

In [ ]:
# Draw the Directed Graph with circular layout where node size = sum of weights of outgoing edges + sum of weights of incoming edges
node_sizes = []
for i in range(1, num_nodes+1):
    incoming_edges = G.in_edges(i, data=True)
    incoming_edges_sum = sum([edge[2]['weight'] for edge in incoming_edges])
    outgoing_edges = G.out_edges(i, data=True)
    outgoing_edges_sum = sum([edge[2]['weight'] for edge in outgoing_edges])
    node_sizes.append(incoming_edges_sum + outgoing_edges_sum)

In [ ]:
data[0]

array([40.        , 30.84632715, 28.93072449])

In [ ]:
pos = nx.circular_layout(G)

# Using Plotly
edge_x = []
edge_y = []
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(x=edge_x, y=edge_y, line=dict(width=0.5, color='#888'), hoverinfo='none', mode='lines')

node_x = []
node_y = []
for node in G.nodes():
    x, y = pos[node]
    node_x.append(x)
    node_y.append(y)

# Node Trace: Color of Node = Node Size As Well
node_trace = go.Scatter(x=node_x, y=node_y, mode='markers', hoverinfo='text', marker=dict(showscale=True, colorscale='YlGnBu', size=node_sizes, colorbar=dict(thickness=15, title='Node Data Throughput', xanchor='left', titleside='right'), line_width=2))

node_text = []
for node in G.nodes():
    node_text.append(f"Total Data Transfer: {round(node_sizes[node-1], 2)}")

node_trace.marker.color = node_sizes
node_trace.text = node_text

fig = go.Figure(data=[edge_trace, node_trace], layout=go.Layout(showlegend=False, hovermode='closest', margin=dict(b=0, l=0, r=0, t=0), xaxis=dict(showgrid=False, zeroline=False, showticklabels=False), yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

fig.show()

Looks Good!

In [ ]:
# Import Isolation Forest
# from sklearn.ensemble import IsolationForest

In [ ]:
# Let's Find Anomalies in the Data array using Isolation Forest
# isolation_forest = IsolationForest(n_estimators=200, random_state=42)
# isolation_forest.fit(data)
# y_pred = isolation_forest.predict(data)

# np.unique(y_pred, return_counts=True)

(array([-1,  1]), array([7966, 2034], dtype=int64))

In [ ]:
# Anomaly Detection using Quantile
data_mean = np.mean(data)
data_std = np.std(data)
threshold = data_mean + 2*data_std

anomalies = data > threshold
anomaly_indices = np.where(anomalies == True)

In [ ]:
anomaly_indices[0]

array([  19,   19,   19, ..., 9983, 9983, 9983], dtype=int64)

In [ ]:
anomalies = anomaly_indices[0]

In [ ]:
anomaly_data = data[anomalies]
normal_data = np.delete(data, anomalies, axis=0)

In [ ]:
anomaly_data.shape, normal_data.shape

((1467, 3), (9511, 3))

In [ ]:
# Display some Anomalies and Normal Data
anomaly_data[:5]

array([[76.570911  , 75.16001773, 79.78717769],
       [76.570911  , 75.16001773, 79.78717769],
       [76.570911  , 75.16001773, 79.78717769],
       [75.15057825, 77.51743507, 76.32111162],
       [75.15057825, 77.51743507, 76.32111162]])

In [ ]:
normal_data[:5]

array([[40.        , 30.84632715, 28.93072449],
       [21.82087998, 30.7061938 , 40.        ],
       [21.62403934, 12.48738915, 40.        ],
       [25.68745832,  7.78671305,  2.14062082],
       [27.33509324, 13.25650089, 10.0039895 ]])

In [ ]:
# Function to Display Graphs
def display_graph(G, existingFigure=None, row=1, col=1):
    pos = nx.circular_layout(G)
    node_sizes = []
    for i in range(1, G.number_of_nodes()+1):
        incoming_edges = G.in_edges(i, data=True)
        incoming_edges_sum = sum([edge[2]['weight'] for edge in incoming_edges])
        outgoing_edges = G.out_edges(i, data=True)
        outgoing_edges_sum = sum([edge[2]['weight'] for edge in outgoing_edges])
        node_sizes.append(incoming_edges_sum + outgoing_edges_sum)

    # Make Node Sizes atleast 0
    node_sizes = np.array(node_sizes)
    if np.min(node_sizes) < 0:
        node_sizes = node_sizes - np.min(node_sizes)

    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.append(x0)
        edge_x.append(x1)
        edge_x.append(None)
        edge_y.append(y0)
        edge_y.append(y1)
        edge_y.append(None)
    edge_trace = go.Scatter(x=edge_x, y=edge_y, line=dict(width=0.5, color='#888'), hoverinfo='none', mode='lines')
    if existingFigure is not None:
        existingFigure.add_trace(edge_trace, row=row, col=col)
    node_x = []
    node_y = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
    node_trace = go.Scatter(x=node_x, y=node_y, mode='markers', hoverinfo='text', marker=dict(showscale=True, colorscale='YlGnBu', size=node_sizes, colorbar=dict(thickness=15, title='Node Data Throughput', xanchor='left', titleside='right'), line_width=2))
    node_text = []
    for node in G.nodes():
        node_text.append(f"Total Data Transfer: {round(node_sizes[node-1], 2)} B")
    node_trace.marker.color = node_sizes
    node_trace.text = node_text
    if existingFigure is not None:
        existingFigure.add_trace(node_trace, row=row, col=col)
    fig = go.Figure(data=[edge_trace, node_trace], layout=go.Layout(showlegend=False, hovermode='closest', margin=dict(b=0, l=0, r=0, t=0), xaxis=dict(showgrid=False, zeroline=False, showticklabels=False), yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))
    return fig

In [ ]:
# Display First Anomaly
G = nx.DiGraph()
G.add_nodes_from(range(1, num_nodes+1))
edges = list(itertools.combinations(range(1, num_nodes+1), 2))
for i in range(len(edges)):
    G.add_edge(edges[i][0], edges[i][1], weight=anomaly_data[0][i])

In [ ]:
fig = display_graph(G)
fig.show()

In [ ]:
# Display First Normal Data
G = nx.DiGraph()
G.add_nodes_from(range(1, num_nodes+1))
edges = list(itertools.combinations(range(1, num_nodes+1), 2))
for i in range(len(edges)):
    G.add_edge(edges[i][0], edges[i][1], weight=normal_data[0][i])

In [ ]:
display_graph(G)

In [ ]:
# Display First 5 Anomalies vs Normal Data using Subplots
from plotly.subplots import make_subplots
fig = make_subplots(rows=5, cols=2, subplot_titles=['Anomaly', 'Normal']*5)

In [ ]:
for i in range(5):
    rand_anomaly = np.random.randint(0, anomaly_data.shape[0])
    random_normal = np.random.randint(0, normal_data.shape[0])
    G = nx.DiGraph()
    G.add_nodes_from(range(1, num_nodes+1))
    edges = list(itertools.combinations(range(1, num_nodes+1), 2))
    for j in range(len(edges)):
        G.add_edge(edges[j][0], edges[j][1], weight=anomaly_data[rand_anomaly][j])
    display_graph(G, fig, row=i+1, col=1)
    G = nx.DiGraph()
    G.add_nodes_from(range(1, num_nodes+1))
    edges = list(itertools.combinations(range(1, num_nodes+1), 2))
    for j in range(len(edges)):
        G.add_edge(edges[j][0], edges[j][1], weight=normal_data[random_normal][j])
    display_graph(G, fig, row=i+1, col=2)

In [ ]:
fig.update_layout(height=2000, width=1000, title_text="Anomalies vs Normal Data")
fig.show()

In [ ]:
# Visualise data array in 3d using plotly
fig = go.Figure(data=[go.Scatter3d(x=anomaly_data[:, 0], y=anomaly_data[:, 1], z=anomaly_data[:, 2], mode='markers', marker=dict(size=4, color='red', opacity=0.8))])
fig.add_trace(go.Scatter3d(x=normal_data[:, 0], y=normal_data[:, 1], z=normal_data[:, 2], mode='markers', marker=dict(size=4, color='blue', opacity=0.8)))
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))
fig.show()

In [ ]:
# Visualise data array in a Histogram of 1st Column
fig = go.Figure()
fig.add_trace(go.Histogram(x=anomaly_data[:, 0], name='Anomaly', marker_color='red'))
fig.add_trace(go.Histogram(x=normal_data[:, 0], name='Normal', marker_color='blue'))
fig.update_layout(barmode='overlay')
fig.update_traces(opacity=0.75)
fig.show()

In [ ]:
# 3D Frequency Heatmap
assert data.shape[1] >= 2

# Create a DataFrame
df = pd.DataFrame(data, columns=['x', 'y', 'z'])
df['freq'] = 1

# Group By x, y, z and Count
df = df.groupby(['x', 'y', 'z']).count().reset_index()

# Create a 3D Scatter Plot
fig = px.scatter_3d(df, x='x', y='y', z='z', size='freq', color='freq', opacity=0.7, title='3D Frequency Heatmap')

fig.show()
